In [110]:
# First I import packages that I will use

import pandas as pd
import numpy as np
import math
import scipy.optimize as opt
from scipy.optimize import minimize
from geopy.distance import vincenty


In [111]:
# Data
data=pd.read_excel('radio_merger_data.xlsx')

data.describe()

year   buyer_id  target_id  buyer_lat  buyer_long  target_lat  \
count    99.000000  99.000000  99.000000  99.000000   99.000000   99.000000   
mean   2007.545455  25.454545  25.454545  36.909475  -94.392918   37.476019   
std       0.500464  14.709620  14.709620   5.068201   13.957259    4.853933   
min    2007.000000   1.000000   1.000000  25.558428 -122.710600   25.369355   
25%    2007.000000  13.000000  13.000000  32.886576 -104.497680   33.687825   
50%    2008.000000  25.000000  25.000000  36.653256  -92.662675   36.900901   
75%    2008.000000  37.500000  37.500000  40.858790  -83.813483   41.145355   
max    2008.000000  54.000000  54.000000  48.704839  -71.411500   48.906401   

       target_long         price  hhi_target  num_stations_buyer  \
count    99.000000  9.900000e+01   99.000000           99.000000   
mean    -94.365015  4.141370e+06   96.353535           18.828283   
std      13.695796  1.471255e+07   82.242463           69.837719   
min    -122.433420  5.724072e+04   10.000000            0.000000   
25%    -104.876615  4.913584e+05   54.500000            1.000000   
50%     -92.122592  1.013110e+06   72.000000            2.000000   
75%     -84.212299  2.330153e+06   91.000000            5.500000   
max     -70.018443  1.393000e+08  388.000000          591.000000   

       population_target  corp_owner_buyer  
count       9.900000e+01         99.000000  
mean        3.229588e+05          0.020202  
std         1.098850e+06          0.141407  
min         2.553000e+03          0.000000  
25%         2.169800e+04          0.000000  
50%         4.994800e+04          0.000000  
75%         1.538550e+05          0.000000  
max         9.818605e+06          1.000000

In [112]:
# we have price in millions of dollar  
data['priceMIL'] = data['price']/1000000

# we have population in millions of numbers 
data['populationMIL'] = data['population_target']/1000000

## PART ONE

In [113]:
# I must set up the data in one array for use in the score function,

# to do so, I define the years and then I create an empty array that will hold all observations and counterfactuals

# for preparing the data for actual and counterfactual matches I devide the data set into 2

years1 = len(data[(data['year']<2008)])
years2 = len(data[(data['year']>2007)])

# now I want to create the observations row by row

# we have 4 equation each with 3 terms so our final matrix should be 2421 * 12

# the equation is :::::      "fm(b,t) = x1bmy1tm + αx2bmy1tm + βdistancebtm + epsilonbtm"

m = 1  
bt = 1
years = years1
arrayone = np.empty((0, 12))

while (m <= 2):
    while (bt <= years-1):
        K = 1
        while (K <= years-bt):
            p1 = (data.iloc[bt-1, 3], data.iloc[bt-1, 4])
            p2 = (data.iloc[bt-1, 5], data.iloc[bt-1, 6])
            p3 = (data.iloc[bt+K-1, 3], data.iloc[bt+K-1, 4])
            p4 = (data.iloc[bt+K-1, 5], data.iloc[bt+K-1, 6])

            x1bmy1tm = data.iloc[bt-1, 9] * data.iloc[bt-1, 12]   #f(b,t)
            x2bmy2tm = data.iloc[bt-1, 11] * data.iloc[bt-1, 12]
            distbtm = vincenty(p1, p2).miles
            

            x1qmy1um = data.iloc[bt+K-1, 9] * data.iloc[bt+K-1, 12]   #f(b',t')
            x2qmy1um = data.iloc[bt+K-1, 11] * data.iloc[bt+K-1, 12]
            distqu = vincenty(p3, p4).miles

            x1bmy1um = data.iloc[bt-1, 9] * data.iloc[bt+K-1, 12]  #f(b',t)   
            x2bmy1um = data.iloc[bt-1, 11] * data.iloc[bt+K-1, 12]
            distbu = vincenty(p1, p4).miles

            x1qmy1tm = data.iloc[bt+K-1, 9] * data.iloc[bt-1, 12]   #f(b,t')
            x2qmy1tm = data.iloc[bt+K-1, 11] * data.iloc[bt-1, 12]
            distqt = vincenty(p3, p2).miles
            
            # I put the observations in the result array
            
            dataforradio = np.array([x1bmy1tm, x2bmy2tm, distbtm, x1qmy1um, x2qmy1um, distqu, x1bmy1um, x2bmy1um, distbu, x1qmy1tm, x2qmy1tm, distqt])
            
            K = K + 1
        
            arrayone = np.append(arrayone, [dataforradio], axis=0)

        bt = bt + 1
    years = years1 + years2 - 1
    m = m + 1

print(arrayone)


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:32: DeprecationWarning: Vincenty is deprecated and is going to be removed in geopy 2.0. Use `geopy.distance.geodesic` (or the default `geopy.distance.distance`) instead, which is more accurate and always converges.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:37: DeprecationWarning: Vincenty is deprecated and is going to be removed in geopy 2.0. Use `geopy.distance.geodesic` (or the default `geopy.distance.distance`) instead, which is more accurate and always converges.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:41: DeprecationWarning: Vincenty is deprecated and is going to be removed in geopy 2.0. Use `geopy.distance.geodesic` (or the default `geopy.distance.distance`) instead, which is more accurate and always converges.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:45: DeprecationWarning: Vincenty is deprecated and is going to be removed in geopy 2.0. Use `ge

[[4.73291730e-01 0.00000000e+00 1.55126597e+02 ... 1.57763910e-01
  0.00000000e+00 8.90117165e+02]
 [4.73291730e-01 0.00000000e+00 1.55126597e+02 ... 1.57763910e-01
  0.00000000e+00 9.69507573e+02]
 [4.73291730e-01 0.00000000e+00 1.55126597e+02 ... 3.15527820e+00
  0.00000000e+00 3.98115140e+02]
 ...
 [1.70202496e+01 0.00000000e+00 5.45523715e+01 ... 4.25506240e+00
  0.00000000e+00 2.14535016e+03]
 [1.70202496e+01 0.00000000e+00 5.45523715e+01 ... 2.12753120e+00
  0.00000000e+00 1.96786397e+02]
 [1.01311012e+00 0.00000000e+00 6.26073453e+02 ... 5.06555060e-01
  0.00000000e+00 1.68377646e+03]]


In [114]:
arrayone.shape

(2421, 12)

In [115]:
# score function

def mse(prms_1, arrayone):
    alpha, beta = prms_1
    sum = 0
    i = 0
    while(i <= len(arrayone)-1):
        # f(b,t)+f(b`,t`)
        f_bt_A = arrayone[i, 0] + alpha * arrayone[i, 1] + beta * arrayone[i, 2] + arrayone[i, 3] + alpha * arrayone[i, 4] + beta * arrayone[i, 5]   
        # f(b`,t)+f(b,t`)
        f_bt_B = arrayone[i, 6] + alpha * arrayone[i, 7] + beta * arrayone[i, 8] + arrayone[i, 9] + alpha * arrayone[i, 10] + beta * arrayone[i, 11]
        # f1>f2
        if f_bt_A > f_bt_B :
            sum = sum - 1

        i = i + 1
        print(sum)
    return sum

# initial guess
b1 = (0.5, -0.5)

# optimization
f_bt1_ = opt.minimize(mse, b1, arrayone, method = 'Nelder-Mead', options={'disp': True})

print(f_bt1_)



-1
-2
-3
-4
-5
-6
-7
-8
-9
-10
-11
-12
-13
-14
-15
-16
-17
-18
-19
-20
-21
-22
-23
-24
-25
-26
-27
-28
-29
-30
-31
-32
-33
-34
-35
-36
-37
-38
-39
-40
-41
-42
-43
-44
-45
-46
-47
-48
-49
-50
-51
-52
-53
-54
-55
-56
-57
-58
-59
-60
-61
-62
-63
-64
-65
-66
-67
-68
-69
-70
-71
-72
-73
-74
-75
-76
-77
-78
-79
-80
-81
-82
-83
-84
-85
-86
-87
-88
-89
-90
-91
-92
-93
-94
-95
-96
-96
-97
-98
-99
-100
-101
-102
-103
-104
-105
-106
-107
-108
-109
-110
-111
-112
-113
-114
-115
-116
-117
-118
-119
-120
-121
-122
-123
-123
-124
-125
-126
-127
-128
-129
-130
-131
-132
-133
-133
-134
-134
-135
-136
-137
-138
-139
-140
-141
-142
-143
-144
-145
-146
-147
-148
-149
-150
-151
-152
-153
-154
-155
-156
-157
-158
-159
-159
-159
-160
-161
-161
-162
-163
-164
-165
-166
-167
-168
-169
-170
-171
-172
-173
-174
-175
-176
-177
-178
-179
-180
-181
-182
-183
-184
-185
-186
-187
-188
-189
-190
-191
-192
-193
-194
-195
-196
-197
-198
-199
-200
-201
-202
-203
-204
-205
-206
-207
-207
-208
-209
-210
-211
-212
-213
-214

-211
-212
-213
-214
-215
-216
-217
-218
-219
-220
-221
-222
-223
-224
-225
-226
-227
-228
-229
-230
-231
-232
-233
-234
-235
-236
-237
-238
-239
-240
-241
-242
-243
-244
-245
-246
-247
-248
-249
-250
-251
-252
-253
-254
-255
-256
-257
-258
-259
-260
-261
-262
-263
-264
-265
-266
-267
-268
-269
-270
-271
-272
-273
-274
-275
-276
-276
-277
-278
-278
-279
-280
-281
-282
-283
-284
-285
-286
-287
-288
-289
-290
-291
-292
-293
-294
-295
-296
-297
-298
-299
-300
-301
-302
-303
-304
-305
-306
-307
-308
-308
-309
-310
-311
-312
-313
-314
-314
-315
-315
-316
-317
-318
-319
-320
-321
-322
-323
-324
-325
-326
-327
-328
-329
-330
-331
-332
-333
-334
-335
-335
-336
-337
-337
-338
-339
-340
-341
-342
-343
-344
-345
-346
-347
-348
-349
-350
-351
-352
-353
-354
-355
-356
-357
-358
-359
-360
-361
-362
-363
-364
-365
-366
-367
-368
-369
-370
-371
-372
-373
-374
-375
-376
-377
-378
-379
-380
-380
-380
-381
-382
-383
-384
-384
-385
-386
-386
-387
-388
-389
-390
-391
-392
-392
-393
-394
-395
-396
-397
-398


-2142
-2143
-2144
-2145
-2146
-2147
-2148
-2149
-2150
-2151
-2152
-2153
-2154
-2155
-2156
-2157
-2158
-2159
-2160
-2161
-2162
-2163
-2164
-2165
-2166
-2167
-2168
-2169
-2170
-2171
-2172
-2173
-2174
-2175
-2176
-2177
-2178
-2179
-2180
-2181
-2182
-2183
-2184
-2185
-2186
-2187
-2188
-2189
-2190
-2191
-2192
-2193
-2194
-2195
-2196
-2197
-2198
-2199
-2200
-2201
-2202
-2203
-2204
-2205
-2206
-2207
-2208
-2209
-2210
-2211
-2212
-2213
-2214
-2215
-2216
-2217
-2218
-2219
-2220
-2221
-2222
-2223
-2224
-2225
-2226
-2227
-2228
-2229
-2230
-2231
-2232
-2233
-2234
-2235
-2236
-2237
-2238
-2239
-2240
-2240
-2241
-2242
-2243
-2244
-2245
-2246
-2247
-2248
-2249
-2250
-2251
-2252
-2253
-2254
-2255
-2256
-2257
-2258
-2259
-2260
-2261
-2262
-2263
-2264
-2265
-2266
-2267
-2268
-2269
-2270
-2271
-1
-2
-3
-4
-5
-6
-7
-8
-9
-10
-11
-12
-13
-14
-15
-16
-17
-18
-19
-20
-21
-22
-23
-24
-25
-26
-27
-28
-29
-30
-31
-32
-33
-34
-35
-36
-37
-38
-39
-40
-41
-42
-43
-44
-45
-46
-47
-48
-49
-50
-51
-52
-53
-54
-55
-56

-1821
-1822
-1823
-1824
-1825
-1826
-1827
-1828
-1829
-1830
-1831
-1832
-1833
-1834
-1835
-1836
-1837
-1838
-1839
-1839
-1840
-1841
-1841
-1842
-1843
-1844
-1845
-1846
-1847
-1848
-1849
-1850
-1851
-1852
-1853
-1854
-1855
-1856
-1857
-1858
-1858
-1859
-1859
-1860
-1861
-1862
-1863
-1864
-1864
-1865
-1866
-1867
-1868
-1869
-1869
-1870
-1871
-1871
-1872
-1873
-1873
-1874
-1874
-1875
-1875
-1875
-1876
-1877
-1877
-1877
-1877
-1878
-1879
-1880
-1881
-1882
-1882
-1883
-1884
-1885
-1886
-1887
-1888
-1889
-1890
-1891
-1892
-1893
-1894
-1895
-1896
-1897
-1897
-1898
-1899
-1900
-1901
-1902
-1903
-1904
-1905
-1906
-1907
-1908
-1909
-1910
-1911
-1912
-1913
-1914
-1915
-1916
-1917
-1918
-1919
-1920
-1921
-1922
-1923
-1924
-1925
-1926
-1927
-1928
-1929
-1930
-1931
-1932
-1933
-1933
-1934
-1935
-1936
-1937
-1938
-1939
-1940
-1941
-1942
-1943
-1944
-1945
-1946
-1947
-1948
-1949
-1950
-1951
-1952
-1953
-1953
-1954
-1955
-1956
-1957
-1958
-1959
-1960
-1961
-1962
-1963
-1964
-1965
-1966
-1967
-1968
-196

-1744
-1745
-1746
-1747
-1748
-1749
-1750
-1751
-1752
-1753
-1754
-1755
-1756
-1757
-1758
-1759
-1760
-1761
-1762
-1763
-1764
-1765
-1766
-1767
-1768
-1769
-1770
-1771
-1772
-1773
-1774
-1774
-1775
-1776
-1777
-1778
-1779
-1780
-1781
-1782
-1783
-1784
-1785
-1786
-1787
-1788
-1789
-1790
-1791
-1792
-1793
-1794
-1795
-1796
-1797
-1798
-1799
-1800
-1801
-1802
-1803
-1804
-1805
-1806
-1807
-1808
-1809
-1810
-1811
-1812
-1813
-1814
-1815
-1816
-1817
-1818
-1819
-1820
-1821
-1822
-1823
-1824
-1825
-1826
-1827
-1828
-1829
-1830
-1831
-1832
-1833
-1834
-1835
-1836
-1837
-1838
-1839
-1839
-1840
-1841
-1841
-1842
-1843
-1844
-1845
-1846
-1847
-1848
-1849
-1850
-1851
-1852
-1853
-1854
-1855
-1856
-1857
-1858
-1858
-1859
-1859
-1860
-1861
-1862
-1863
-1864
-1864
-1865
-1866
-1867
-1868
-1869
-1869
-1870
-1871
-1871
-1872
-1873
-1873
-1874
-1874
-1875
-1875
-1875
-1876
-1877
-1877
-1877
-1877
-1878
-1879
-1880
-1881
-1882
-1882
-1883
-1884
-1885
-1886
-1887
-1888
-1889
-1890
-1891
-1892
-1893
-189

...

-458
-459
-460
-461
-461
-462
-462
-462
-463
-463
-463
-464
-465
-466
-467
-468
-469
-470
-471
-472
-473
-474
-475
-476
-477
-478
-479
-480
-481
-482
-483
-484
-485
-486
-487
-488
-489
-490
-491
-492
-493
-494
-495
-496
-497
-498
-499
-500
-501
-502
-503
-504
-505
-506
-507
-508
-509
-510
-511
-512
-513
-514
-515
-516
-517
-518
-519
-519
-520
-521
-522
-523
-524
-525
-526
-527
-528
-529
-530
-531
-532
-533
-534
-535
-536
-537
-538
-539
-540
-541
-542
-543
-544
-545
-546
-547
-547
-548
-549
-549
-550
-551
-552
-553
-554
-555
-556
-557
-558
-559
-560
-561
-562
-563
-564
-565
-566
-567
-568
-569
-570
-571
-572
-573
-574
-575
-576
-577
-578
-579
-580
-581
-582
-583
-584
-585
-586
-587
-588
-589
-590
-591
-592
-593
-594
-595
-596
-597
-598
-599
-600
-600
-601
-602
-603
-604
-605
-606
-607
-608
-609
-610
-611
-612
-613
-614
-615
-616
-617
-618
-619
-620
-621
-622
-623
-624
-625
-626
-627
-628
-629
-630
-631
-632
-633
-634
-635
-636
-637
-638
-639
-640
-641
-642
-643
-644
-645
-646
-647
-648


-356
-357
-358
-359
-360
-361
-362
-363
-364
-365
-366
-367
-368
-369
-370
-371
-372
-373
-374
-375
-376
-377
-378
-379
-380
-381
-382
-382
-382
-383
-384
-385
-386
-386
-387
-388
-388
-389
-390
-391
-392
-393
-394
-394
-395
-396
-397
-398
-399
-400
-401
-402
-402
-402
-403
-403
-404
-405
-405
-406
-407
-408
-409
-410
-410
-411
-412
-413
-414
-415
-416
-417
-418
-419
-420
-421
-422
-423
-424
-425
-426
-427
-428
-429
-430
-431
-432
-433
-434
-435
-436
-436
-437
-438
-439
-440
-441
-442
-443
-444
-445
-446
-447
-448
-449
-450
-451
-452
-453
-453
-454
-455
-456
-457
-458
-459
-460
-461
-461
-462
-462
-462
-463
-463
-463
-464
-465
-466
-467
-468
-469
-470
-471
-472
-473
-474
-475
-476
-477
-478
-479
-480
-481
-482
-483
-484
-485
-486
-487
-488
-489
-490
-491
-492
-493
-494
-495
-496
-497
-498
-499
-500
-501
-502
-503
-504
-505
-506
-507
-508
-509
-510
-511
-512
-513
-514
-515
-516
-517
-518
-519
-519
-520
-521
-522
-523
-524
-525
-526
-527
-528
-529
-530
-531
-532
-533
-534
-535
-536
-537


-274
-275
-276
-277
-277
-278
-279
-279
-280
-281
-282
-283
-284
-285
-286
-287
-288
-289
-290
-291
-292
-293
-294
-295
-296
-297
-298
-299
-300
-301
-302
-303
-304
-305
-306
-307
-308
-309
-309
-310
-311
-312
-313
-314
-315
-315
-316
-316
-317
-318
-319
-320
-321
-322
-323
-324
-325
-326
-327
-328
-329
-330
-331
-332
-333
-334
-335
-336
-337
-338
-339
-339
-340
-341
-342
-343
-344
-345
-346
-347
-348
-349
-350
-351
-352
-353
-354
-355
-356
-357
-358
-359
-360
-361
-362
-363
-364
-365
-366
-367
-368
-369
-370
-371
-372
-373
-374
-375
-376
-377
-378
-379
-380
-381
-382
-382
-382
-383
-384
-385
-386
-386
-387
-388
-388
-389
-390
-391
-392
-393
-394
-394
-395
-396
-397
-398
-399
-400
-401
-402
-402
-402
-403
-403
-404
-405
-405
-406
-407
-408
-409
-410
-410
-411
-412
-413
-414
-415
-416
-417
-418
-419
-420
-421
-422
-423
-424
-425
-426
-427
-428
-429
-430
-431
-432
-433
-434
-435
-436
-436
-437
-438
-439
-440
-441
-442
-443
-444
-445
-446
-447
-448
-449
-450
-451
-452
-453
-453
-454
-455


-178
-179
-180
-181
-182
-183
-184
-185
-186
-187
-188
-189
-190
-191
-192
-193
-194
-195
-196
-197
-198
-199
-200
-201
-202
-203
-204
-205
-206
-207
-208
-208
-209
-210
-211
-212
-213
-214
-215
-216
-217
-218
-219
-220
-221
-222
-223
-224
-225
-226
-227
-228
-229
-230
-231
-232
-233
-234
-235
-236
-237
-238
-239
-240
-241
-242
-243
-244
-245
-246
-247
-248
-249
-250
-251
-252
-253
-254
-255
-256
-257
-258
-259
-260
-261
-262
-263
-264
-265
-266
-267
-268
-269
-270
-271
-272
-273
-274
-275
-276
-277
-277
-278
-279
-279
-280
-281
-282
-283
-284
-285
-286
-287
-288
-289
-290
-291
-292
-293
-294
-295
-296
-297
-298
-299
-300
-301
-302
-303
-304
-305
-306
-307
-308
-309
-309
-310
-311
-312
-313
-314
-315
-315
-316
-316
-317
-318
-319
-320
-321
-322
-323
-324
-325
-326
-327
-328
-329
-330
-331
-332
-333
-334
-335
-336
-337
-338
-339
-339
-340
-341
-342
-343
-344
-345
-346
-347
-348
-349
-350
-351
-352
-353
-354
-355
-356
-357
-358
-359
-360
-361
-362
-363
-364
-365
-366
-367
-368
-369
-370


-2231
-2232
-2233
-2234
-2235
-2236
-2237
-2238
-2239
-2240
-2241
-2242
-2243
-2244
-2245
-2246
-2247
-2248
-2249
-2250
-2251
-2252
-2253
-2253
-2254
-2255
-2256
-2257
-2258
-2259
-2260
-2261
-2262
-2263
-2264
-2265
-2266
-2267
-2268
-2269
-2270
-2271
-2272
-2273
-2274
-2275
-2276
-2277
-2278
-2279
-2280
-2281
-2282
-2283
-2284
Optimization terminated successfully.
         Current function value: -2284.000000
         Iterations: 18
         Function evaluations: 51
 final_simplex: (array([[ 0.3625    , -0.775     ],
       [ 0.36254883, -0.775     ],
       [ 0.36247559, -0.77509766]]), array([-2284., -2284., -2284.]))
           fun: -2284.0
       message: 'Optimization terminated successfully.'
          nfev: 51
           nit: 18
        status: 0
       success: True
             x: array([ 0.3625, -0.775 ])


## PART TWO

In [116]:
# in this part I include prices and the HHI index 

# again I want to create the observations row by row

# we have 4 equation each with 5 terms so our final matrix should be 2421 * 20

# the equation is ::::::  "fm(b,t) = δx1bmy1tm + αx2bmy1tm + γHHItm + βdistancebtm + epsilonbtm"

years1 = len(data[(data['year']<2008)])
years2 = len(data[(data['year']>2007)])

m = 1  
bt = 1
years = years1
arraytwo = np.empty((0, 20))

while (m <= 2):
    while (bt <= years-1):
        K = 1
        while (K <= years-bt):
            p1 = (data.iloc[bt-1, 3], data.iloc[bt-1, 4])
            p2 = (data.iloc[bt-1, 5], data.iloc[bt-1, 6])
            p3 = (data.iloc[bt+K-1, 3], data.iloc[bt+K-1, 4])
            p4 = (data.iloc[bt+K-1, 5], data.iloc[bt+K-1, 6])

            x1bmy1tm = data.iloc[bt-1, 9] * data.iloc[bt-1, 12]   #f(b,t)
            x2bmy2tm = data.iloc[bt-1, 11] * data.iloc[bt-1, 12]
            hhibtm = data.iloc[bt-1, 8]
            distbtm = vincenty(p1, p2).miles
            

            x1qmy1um = data.iloc[bt+K-1, 9] * data.iloc[bt+K-1, 12]   #f(b',t')
            x2qmy1um = data.iloc[bt+K-1, 11] * data.iloc[bt+K-1, 12]
            hhiqu = data.iloc[bt-1, 8]
            distqu = vincenty(p3, p4).miles

            x1bmy1um = data.iloc[bt-1, 9] * data.iloc[bt+K-1, 12]  #f(b',t)   
            x2bmy1um = data.iloc[bt-1, 11] * data.iloc[bt+K-1, 12]
            hhibu = data.iloc[bt+K-1, 8]
            distbu = vincenty(p1, p4).miles

            x1qmy1tm = data.iloc[bt+K-1, 9] * data.iloc[bt-1, 12]   #f(b,t')
            x2qmy1tm = data.iloc[bt+K-1, 11] * data.iloc[bt-1, 12]
            hhigt = data.iloc[bt+K-1, 8]
            distqt = vincenty(p3, p2).miles
            
            # p(b,t) and p(b`,t`)
            price_11 = data.iloc[bt-1, 13]
            price_22 = data.iloc[bt+K-1, 13]

            dataforradio = np.array([x1bmy1tm, x2bmy2tm, hhibtm, distbtm, x1qmy1um, x2qmy1um, hhiqu, distqu, price_11, price_22, x1bmy1um, x2bmy1um, hhibu, distbu, x1qmy1tm, x2qmy1tm, hhigt, distqt, price_11, price_22])
            
            K = K + 1
            
# I put the observations in the result array
            
            arraytwo = np.append(arraytwo, [dataforradio], axis=0)

        bt = bt + 1
    years = years1 + years2 - 1

    m = m + 1

print(arraytwo)


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:29: DeprecationWarning: Vincenty is deprecated and is going to be removed in geopy 2.0. Use `geopy.distance.geodesic` (or the default `geopy.distance.distance`) instead, which is more accurate and always converges.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:35: DeprecationWarning: Vincenty is deprecated and is going to be removed in geopy 2.0. Use `geopy.distance.geodesic` (or the default `geopy.distance.distance`) instead, which is more accurate and always converges.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:40: DeprecationWarning: Vincenty is deprecated and is going to be removed in geopy 2.0. Use `geopy.distance.geodesic` (or the default `geopy.distance.distance`) instead, which is more accurate and always converges.
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:45: DeprecationWarning: Vincenty is deprecated and is going to be removed in geopy 2.0. Use `ge

[[4.73291730e-01 0.00000000e+00 8.00000000e+01 ... 8.90117165e+02
  2.16760000e-02 1.15390000e-02]
 [4.73291730e-01 0.00000000e+00 8.00000000e+01 ... 9.69507573e+02
  2.16760000e-02 1.82265000e-01]
 [4.73291730e-01 0.00000000e+00 8.00000000e+01 ... 3.98115140e+02
  2.16760000e-02 2.03065000e-01]
 ...
 [1.70202496e+01 0.00000000e+00 3.40000000e+01 ... 2.14535016e+03
  2.94050000e-02 5.13340000e-02]
 [1.70202496e+01 0.00000000e+00 3.40000000e+01 ... 1.96786397e+02
  2.94050000e-02 1.49618000e-01]
 [1.01311012e+00 0.00000000e+00 1.64000000e+02 ... 1.68377646e+03
  5.13340000e-02 1.49618000e-01]]


In [117]:
arraytwo.shape

(2421, 20)

In [118]:

#score function
def mse2(prms_2, arraytwo):
    delta, alpha, gamma, beta = prms_2
    sum = 0
    i = 0
    while(i <= len(arraytwo)-1):
        f_bt_A = delta * arraytwo[i, 0] + alpha * arraytwo[i, 1] + gamma * arraytwo[i, 2] + beta * arraytwo[i, 3] + arraytwo[i, 9] - delta * arraytwo[i, 10] - alpha * arraytwo[i, 11] - gamma * arraytwo[i, 12] - beta * arraytwo[i, 13] - arraytwo[i, 18]
    
        f_bt_B = delta * arraytwo[i, 4] + alpha * arraytwo[i, 5] + gamma * arraytwo[i, 6] + beta * arraytwo[i, 7] + arraytwo[i, 8] - delta * arraytwo[i, 14] - alpha * arraytwo[i, 15] - gamma * arraytwo[i, 16] - beta * arraytwo[i, 17] - arraytwo[i, 19]
        
     
        if f_bt_A > f_bt_B :
            sum = sum - 1

        i = i + 1
        
        print(sum)
        
    return sum

"Initial Guess"
b1 = (0.5, 1, 1, -0.5 )

"Optimization routine"
f_bt_2 = opt.minimize(mse2, b1, arraytwo, method = 'Nelder-Mead', options={'disp': True})

print(f_bt_2)

0
-1
-2
-2
-2
-3
-3
-4
-4
-5
-6
-7
-8
-9
-10
-11
-11
-11
-12
-13
-14
-15
-15
-15
-15
-15
-15
-15
-15
-15
-15
-15
-16
-16
-16
-17
-18
-19
-20
-20
-21
-22
-23
-24
-24
-25
-25
-26
-27
-27
-27
-28
-29
-30
-31
-32
-33
-34
-34
-34
-34
-35
-36
-37
-38
-39
-40
-41
-41
-41
-41
-42
-43
-43
-43
-44
-45
-45
-46
-47
-48
-49
-50
-51
-52
-52
-53
-54
-55
-55
-56
-56
-57
-58
-59
-60
-61
-62
-63
-64
-65
-65
-65
-66
-66
-67
-68
-69
-70
-71
-72
-72
-72
-72
-73
-74
-75
-76
-77
-77
-78
-78
-79
-79
-80
-80
-81
-82
-83
-83
-83
-83
-83
-84
-84
-85
-85
-86
-86
-86
-87
-87
-87
-87
-87
-87
-88
-88
-88
-88
-88
-88
-88
-88
-88
-88
-88
-88
-89
-89
-89
-90
-91
-91
-91
-92
-92
-93
-93
-93
-93
-94
-94
-94
-95
-96
-97
-98
-98
-99
-100
-101
-101
-101
-102
-103
-104
-105
-105
-106
-107
-108
-108
-108
-108
-108
-109
-110
-111
-112
-113
-114
-115
-115
-116
-117
-118
-119
-119
-120
-120
-120
-121
-122
-123
-124
-125
-126
-127
-128
-129
-129
-129
-130
-131
-132
-132
-133
-134
-134
-134
-134
-134
-135
-136
-137
-137
-138
-139


-989
-990
-990
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-991
-992
-992
-992
-992
-992
-993
-993
-994
-995
-995
-995
-995
-995
-996
-996
-997
-998
-999
-1000
-1000
-1000
-1000
-1000
-1001
-1002
-1002
-1003
-1004
-1004
-1005
-1006
-1007
-1007
-1008
-1009
-1010
-1011
-1012
-1013
-1014
-1015
-1016
-1017
-1018
-1019
-1020
-1021
-1022
-1023
-1023
-1023
-1024
-1024
-1024
-1024
-1025
-1026
-1027
-1028
-1029
-1029
-1030
-1030
-1030
-1030
-1030
-1031
-1031
-1032
-1032
-1033
-1034
-1035
-1035
-1036
-1037
-1038
-1039
-1040
-1041
-1042
-1043
-1044
-1045
-1046
-1047
-1048
-1049
-1050
-1051
-1051
-1051
-1051
-1051
-1051
-1052
-1052
-1053
-1054
-1055
-1056
-1056
-1056
-1056
-1056
-1057
-1058
-1058
-1059
-1059
-1059
-1059
-1059
-1059
-1059
-1059
-1059
-1059
-1060
-1060
-1060
-1061
-1061
-1062
-1062
-1062
-1062
-1062
-1062
-1062
-1062
-1063
-1064
-1065
-1065
-1066
-1067
-1067
-1068
-1069
-1070
-1070
-1070
-1071
-1072
-1073
-1074
-1075
-1076

-822
-822
-822
-822
-822
-822
-822
-822
-822
-822
-822
-822
-822
-822
-822
-823
-823
-823
-823
-823
-823
-823
-823
-823
-823
-823
-824
-825
-826
-826
-826
-827
-828
-829
-829
-829
-830
-831
-832
-833
-833
-834
-834
-835
-836
-836
-836
-836
-836
-837
-837
-838
-839
-840
-841
-841
-841
-841
-841
-841
-842
-842
-842
-843
-844
-844
-844
-845
-846
-847
-848
-849
-850
-851
-852
-852
-852
-853
-853
-854
-854
-854
-854
-854
-855
-856
-856
-857
-858
-859
-860
-860
-860
-861
-861
-862
-863
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-864
-865
-865
-865
-865
-865
-865
-865
-865
-865
-865
-865
-865
-865
-865
-865
-866
-866
-866
-866
-866
-867
-868
-868
-868
-868
-868
-868
-868
-868
-868
-868
-869
-869
-869
-870
-870
-870
-871
-871
-871
-871
-871
-872
-872
-873
-873
-873
-874
-875
-876
-876
-877
-878
-879
-880
-881
-881
-882
-882
-883
-884
-884
-884
-884
-885
-886
-886
-887
-888
-889
-890
-890
-890
-891
-892
-893
-893
-893


-716
-716
-717
-717
-717
-717
-718
-718
-719
-720
-720
-720
-721
-722
-722
-722
-722
-723
-723
-724
-724
-724
-725
-725
-726
-727
-727
-727
-728
-729
-729
-729
-730
-731
-732
-732
-732
-733
-734
-735
-736
-736
-737
-737
-737
-738
-738
-738
-738
-738
-739
-739
-740
-741
-741
-742
-743
-743
-743
-743
-743
-743
-743
-744
-745
-746
-747
-748
-749
-750
-751
-752
-753
-754
-755
-756
-757
-758
-759
-760
-761
-762
-763
-764
-765
-766
-767
-768
-769
-769
-770
-771
-772
-773
-774
-775
-776
-777
-778
-779
-780
-781
-782
-783
-784
-785
-786
-786
-787
-787
-787
-788
-788
-788
-788
-788
-788
-788
-788
-788
-788
-789
-789
-789
-789
-789
-789
-789
-789
-789
-789
-789
-790
-790
-790
-791
-791
-791
-791
-791
-791
-791
-791
-791
-791
-792
-792
-793
-794
-794
-794
-795
-795
-795
-795
-795
-796
-797
-798
-798
-799
-800
-801
-801
-801
-801
-801
-801
-802
-802
-802
-802
-803
-804
-805
-806
-807
-807
-808
-808
-808
-808
-808
-809
-810
-811
-811
-812
-812
-812
-813
-814
-814
-814
-814
-815
-815
-815
-815
-816


-536
-536
-537
-537
-538
-538
-538
-538
-538
-538
-538
-538
-538
-538
-538
-539
-539
-539
-540
-540
-541
-541
-541
-541
-541
-541
-541
-541
-541
-541
-541
-541
-542
-543
-544
-544
-545
-545
-546
-546
-547
-548
-548
-548
-549
-550
-550
-550
-550
-551
-552
-552
-552
-553
-554
-555
-555
-555
-555
-555
-556
-556
-556
-556
-556
-556
-557
-558
-559
-560
-560
-561
-561
-561
-561
-561
-562
-563
-563
-563
-564
-565
-566
-567
-568
-568
-569
-569
-570
-571
-572
-573
-574
-575
-576
-577
-578
-579
-580
-581
-582
-583
-584
-585
-586
-587
-588
-588
-589
-589
-590
-591
-591
-591
-591
-592
-592
-592
-593
-593
-594
-595
-596
-596
-597
-598
-599
-599
-600
-601
-602
-603
-604
-605
-605
-606
-606
-607
-608
-609
-610
-611
-611
-612
-612
-612
-613
-613
-614
-615
-616
-616
-616
-617
-618
-618
-618
-618
-619
-620
-621
-622
-622
-622
-623
-624
-625
-626
-627
-627
-628
-629
-629
-630
-630
-631
-632
-633
-633
-634
-635
-636
-636
-637
-637
-637
-637
-638
-639
-640
-640
-641
-641
-641
-641
-641
-642
-643
-644
-644


...

-1016
-1017
-1018
-1019
-1020
-1021
-1022
-1023
-1024
-1024
-1024
-1025
-1025
-1025
-1025
-1026
-1027
-1028
-1029
-1030
-1030
-1031
-1031
-1031
-1031
-1031
-1032
-1032
-1033
-1033
-1034
-1035
-1036
-1036
-1037
-1038
-1039
-1040
-1041
-1042
-1043
-1044
-1045
-1046
-1047
-1048
-1049
-1050
-1051
-1052
-1052
-1052
-1052
-1052
-1052
-1053
-1053
-1054
-1055
-1056
-1057
-1057
-1057
-1057
-1057
-1058
-1059
-1059
-1060
-1060
-1060
-1060
-1060
-1060
-1060
-1060
-1060
-1060
-1061
-1061
-1061
-1062
-1062
-1063
-1063
-1063
-1063
-1063
-1063
-1063
-1063
-1064
-1065
-1066
-1066
-1067
-1068
-1068
-1069
-1070
-1071
-1071
-1071
-1072
-1073
-1074
-1075
-1076
-1077
-1078
-1079
-1080
-1081
-1082
-1083
-1084
-1085
-1086
-1087
-1088
-1089
-1090
-1091
-1092
-1093
-1094
-1095
-1096
-1097
-1098
-1099
-1100
-1101
-1102
-1103
-1104
-1105
-1106
-1107
-1108
-1109
-1109
-1109
-1110
-1110
-1111
-1112
-1112
-1112
-1113
-1113
-1114
-1114
-1115
-1115
-1115
-1115
-1115
-1115
-1115
-1115
-1115
-1115
-1116
-1116
-1117
-111

-937
-937
-937
-937
-937
-937
-937
-938
-938
-939
-939
-939
-939
-940
-940
-941
-941
-941
-942
-942
-942
-942
-942
-942
-942
-942
-942
-942
-942
-942
-942
-943
-943
-943
-943
-943
-943
-943
-943
-943
-943
-944
-945
-946
-947
-947
-947
-947
-948
-949
-950
-950
-950
-950
-951
-952
-953
-954
-954
-955
-956
-957
-958
-959
-960
-961
-961
-961
-962
-963
-964
-965
-965
-966
-966
-967
-968
-969
-969
-969
-970
-971
-972
-973
-974
-974
-975
-976
-976
-977
-977
-978
-979
-980
-980
-981
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-983
-983
-983
-983
-983
-984
-984
-984
-984
-985
-985
-985
-985
-985
-985
-986
-986
-986
-986
-986
-987
-988
-989
-990
-990
-990
-990
-990
-990
-990
-991
-991
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-993
-993
-993
-993
-993
-994
-994
-995
-996
-996
-996
-996
-996
-997
-997
-998
-999
-1000
-1001
-1001
-1001
-1001
-1001
-1002
-1003
-1003
-1004
-1005
-1005
-1006
-1007
-

-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-982
-983
-983
-983
-983
-983
-984
-984
-984
-984
-985
-985
-985
-985
-985
-985
-986
-986
-986
-986
-986
-987
-988
-989
-990
-990
-990
-990
-990
-990
-990
-991
-991
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-992
-993
-993
-993
-993
-993
-994
-994
-995
-996
-996
-996
-996
-996
-997
-997
-998
-999
-1000
-1001
-1001
-1001
-1001
-1001
-1002
-1003
-1003
-1004
-1005
-1005
-1006
-1007
-1008
-1008
-1009
-1010
-1011
-1012
-1013
-1014
-1015
-1016
-1017
-1018
-1019
-1020
-1021
-1022
-1023
-1024
-1024
-1024
-1025
-1025
-1025
-1025
-1026
-1027
-1028
-1029
-1030
-1030
-1031
-1031
-1031
-1031
-1031
-1032
-1032
-1033
-1033
-1034
-1035
-1036
-1036
-1037
-1038
-1039
-1040
-1041
-1042
-1043
-1044
-1045
-1046
-1047
-1048
-1049
-1050
-1051
-1052
-1052
-1052
-1052
-1052
-1052
-1053
-1053
-1054
-1055
-1056
-1057
-1057
-1057
-1057
-1057
-1058
-1059
-1059
-1060
-1060
-1060
-

-873
-874
-875
-876
-876
-877
-878
-879
-880
-881
-881
-882
-882
-883
-884
-884
-884
-884
-885
-886
-887
-888
-889
-890
-891
-891
-891
-892
-893
-894
-894
-894
-894
-894
-895
-896
-896
-896
-897
-898
-899
-900
-900
-901
-901
-902
-903
-904
-904
-904
-905
-906
-907
-908
-909
-909
-910
-911
-911
-912
-913
-914
-915
-915
-916
-917
-918
-919
-920
-921
-922
-923
-923
-923
-924
-924
-925
-926
-926
-926
-926
-927
-927
-928
-929
-930
-931
-932
-933
-933
-934
-934
-935
-935
-936
-936
-936
-936
-936
-936
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-937
-938
-938
-939
-939
-939
-939
-940
-940
-941
-941
-941
-942
-942
-942
-942
-942
-942
-942
-942
-942
-942
-942
-942
-942
-943
-943
-943
-943
-943
-943
-943
-943
-943
-943
-944
-945
-946
-947
-947
-947
-947
-948
-949
-950
-950
-950
-950
-951
-952
-953
-954
-954
-955
-956
-957
-958
-959
-960
-961
-961
-961
-962
-963
-964
-965
-965
-966
-966
-967
-968
-969
-969
-969
-970
-971
-972
-973
-974


-290
-291
-292
-293
-294
-295
-296
-297
-298
-299
-300
-301
-302
-303
-303
-304
-304
-305
-306
-307
-308
-309
-310
-311
-312
-313
-314
-315
-316
-317
-318
-319
-319
-319
-319
-319
-319
-319
-319
-319
-319
-319
-320
-320
-320
-321
-321
-321
-321
-322
-322
-323
-324
-324
-325
-325
-326
-327
-328
-328
-329
-329
-329
-329
-329
-329
-329
-330
-330
-331
-332
-332
-333
-334
-335
-336
-337
-337
-338
-339
-340
-340
-340
-340
-340
-340
-340
-340
-340
-341
-341
-341
-342
-342
-342
-343
-344
-344
-345
-345
-345
-346
-346
-346
-347
-348
-349
-349
-349
-350
-351
-352
-352
-352
-353
-354
-354
-355
-356
-357
-358
-359
-359
-360
-360
-361
-361
-361
-361
-361
-361
-361
-361
-362
-362
-363
-363
-364
-365
-366
-366
-367
-367
-367
-368
-368
-369
-369
-369
-369
-369
-369
-369
-370
-370
-371
-372
-372
-373
-374
-374
-375
-375
-375
-376
-376
-377
-377
-377
-377
-377
-378
-378
-378
-379
-380
-381
-382
-383
-384
-385
-386
-386
-387
-387
-388
-388
-389
-390
-391
-391
-391
-392
-393
-393
-394
-395
-396
-397
-398
